# Munich to Budapest -  Example for openrouteservice direction module

### avoiding borders and using tollroads as well as avoiding tollroads

First import all needed packages.

In [1]:
import folium
from folium import FeatureGroup, LayerControl, Map, Marker

from pprint import pprint

from openrouteservice import client#, places, geocoding
from openrouteservice.directions import directions

In [2]:
api_key = '58d904a497c67e00015b45fc2a6b6872037d44119582ef40cdf264c4' # individual api key
clnt = client.Client(key=api_key) # creating client with api key

map1 = folium.Map(tiles='OpenStreetMap', location=([48.57479, 15.46875]), zoom_start=7) 

In [3]:
# creating feature groups
#tollhgv_group = FeatureGroup(name='Tollroute for hgv') 
#tollcar_group = FeatureGroup(name='Tollroute for cars') 
#freehgv_group = FeatureGroup(name='Tollfree route for hgv')
#feecar_group = FeatureGroup(name='Tollfree route for cars')

In [210]:
new_dict = {'hgv': {'profile': 'driving-hgv'}, # vehicle, profile
           'car': {'profile': 'driving-car'}}

vehicle_profile = {'hgv_profile': 'driving-hgv',
                   'car_profile': 'driving-car'}

#avoid_options = {'avoid_features': 'tollways'}

params_route = {'coordinates': [[11.544056, 48.151543], [19.092865, 47.514882]],
               'format_out': 'geojson',
               'geometry': 'true',
               'geometry_format': 'geojson',
               'preference': 'fastest',
                'instructions': 'true',
               'options': {'avoid_countries': '11'}}

params_route_extra = {'coordinates': [[11.544056, 48.151543], [19.092865, 47.514882]],
                      'geometry': 'true',
                      'preference': 'fastest',
                      'instructions': 'false',
                      'extra_info': {'tollways'},
                      'options': {'avoid_countries': '11'}}

style_dict = {'hgv': 'orange',
             'car': 'yellow'}

style_dict_new = {'tollroad': {'hgv': {'orange'}, # road_type, vehicle_style
                               'car': {'yellow'}},
                  'tollfree': {'hgv': {'lightblue'},
                              'car': {'#ff9999'}}}

In [220]:
for road_type, vehicle_style in style_dict_new.items():
    pprint(vehicle_style)

{'car': {'yellow'}, 'hgv': {'orange'}}
{'car': {'#ff9999'}, 'hgv': {'lightblue'}}


In [213]:
for vehicle, profile in new_dict.items():
    for road_type, vehicle_style, l in style_dict_new.items():
        if vehicle_style in vehicle:
            profile['style'] = style_dict_new['tollroad']
pprint(new_dict)     

TypeError: 'in <string>' requires string as left operand, not dict

In [182]:
for vehicle, profile in new_dict.items():
    for style_vehicle, style in style_dict.items():
        if style_vehicle in vehicle:
            profile['style'] = style
pprint(new_dict)        

In [194]:
map2 = folium.Map(tiles='OpenStreetMap', location=([48.57479, 15.46875]), zoom_start=7) 
for vehicle, profile in new_dict.items():
    for style_vehicle, style in style_dict.items():
        if style_vehicle in vehicle:
            profile['style'] = style
    params_route['profile'] = profile['profile']
    vehicle_route = clnt.directions(**params_route)
    for avoid_country in vehicle_route['features']:
        coords_countries = [[y,x] for x,y in avoid_country['geometry']['coordinates']]
        
        folium.features.PolyLine(coords_countries, color=profile['style'], popup='Tollroad').add_to(map2) # blue roads
map2

In [ ]:
tollroad_array = []
toll_values = []
for vehicle, profile in new_dict.items():
    params_route['profile'] = profile['profile']
    vehicle_route = clnt.directions(**params_route)
    for avoid_country in vehicle_route['features']:
        coords_countries = [[y,x] for x,y in avoid_country['geometry']['coordinates']]
        folium.features.PolyLine(coords_countries, color='blue', popup='Tollroad').add_to(map1) # blue roads
    tollroad_array.append(vehicle_route)

#for a, vehicle in vehicle_profile.items():
    params_route_extra['profile'] = vehicle
    toll_route = clnt.directions(**params_route_extra)
    for value in toll_route['routes']:
        toll_values += [value['extras']['tollways']['values']]
        
route_kombi_dict = {'hgv': [toll_values[0], tollroad_array[0]], 'car': [toll_values[1],  tollroad_array[1]]}

for vehicle in route_kombi_dict:
    for value in route_kombi_dict[vehicle][0]:
        if 1 in value:
            vehicle_value = [value[0:2]]
            
            for i,j in vehicle_value:
                vehicle_coords = [coords['geometry']['coordinates'][i:j] for coords in route_kombi_dict[vehicle][1]['features']]
                               
                for n in vehicle_coords:
                    switched_vehicle_coords = [[y,x] for x,y in n]
                    folium.PolyLine(switched_vehicle_coords, color='#cc0000', popup='Tollroad').add_to(map1) # adding to map #red roads
map1

In [5]:
tollroad_array = []
toll_values = []
for a, vehicle in vehicle_profile.items():
    params_route['profile'] = vehicle
    vehicle_route = clnt.directions(**params_route)
    for avoid_country in vehicle_route['features']:
        coords_countries = [[y,x] for x,y in avoid_country['geometry']['coordinates']]
        folium.features.PolyLine(coords_countries, color='blue', popup='Tollroad').add_to(map1) # blue roads
    tollroad_array.append(vehicle_route)

#for a, vehicle in vehicle_profile.items():
    params_route_extra['profile'] = vehicle
    toll_route = clnt.directions(**params_route_extra)
    for value in toll_route['routes']:
        toll_values += [value['extras']['tollways']['values']]
        
route_kombi_dict = {'hgv': [toll_values[0], tollroad_array[0]], 'car': [toll_values[1],  tollroad_array[1]]}

for vehicle in route_kombi_dict:
    for value in route_kombi_dict[vehicle][0]:
        if 1 in value:
            vehicle_value = [value[0:2]]
            
            for i,j in vehicle_value:
                vehicle_coords = [coords['geometry']['coordinates'][i:j] for coords in route_kombi_dict[vehicle][1]['features']]
                               
                for n in vehicle_coords:
                    switched_vehicle_coords = [[y,x] for x,y in n]
                    folium.PolyLine(switched_vehicle_coords, color='#cc0000', popup='Tollroad').add_to(map1) # adding to map #red roads
map1

In [6]:
for a, vehicle in vehicle_profile.items():
    params_route['profile'] = vehicle
    params_route['options'] = {'avoid_countries': '11', 
                               'avoid_features': 'tollways'}
    tollfree_route = clnt.directions(**params_route)
    for avoid_toll in tollfree_route['features']:
        coords_tollfree = [[y,x] for x,y in avoid_toll['geometry']['coordinates']]
        folium.features.PolyLine(coords_tollfree, color='green', popup='Avoiding tollroad').add_to(map1)
map1

In [27]:
pprint(q)

{'yellow', 'orange'}


In [ ]:
### doesn't print out both toll roads if packed in one code -- whyyy?!
for a, vehicle in vehicle_profile.items():
    params_route['profile'] = vehicle
    vehicle_route = clnt.directions(**params_route)
    for avoid_country in vehicle_route['features']:
        coords_countries = [[y,x] for x,y in avoid_country['geometry']['coordinates']]
        folium.features.PolyLine(coords_countries, color='blue', popup='Avoiding Austria').add_to(map1)
    
    params_route['options'] = {'avoid_countries': '11', 
                               'avoid_features': 'tollways'}
    tollfree_route = clnt.directions(**params_route)
    for avoid_toll in tollfree_route['features']:
        coords_tollfree = [[y,x] for x,y in avoid_toll['geometry']['coordinates']]
        folium.features.PolyLine(coords_tollfree, color='green', popup='Avoiding tollroads').add_to(map1)
    
map1

In [17]:
#pprint(route_tollhgv['routes'][0]['extras']) # infos über distance für toll und tollfree

In [21]:
# requesting extra info data
route_tollhgv = directions(client=clnt, coordinates=([11.544056, 48.151543], [19.092865, 47.514882]), profile='driving-hgv', preference='fastest', extra_info={'tollways'}, options={'avoid_countries':'11'})

In [11]:
# requesting extra infos for toll waypoints
r = requests.get(url='https://api.openrouteservice.org/directions?coordinates=11.544056%2C48.151543%7C19.092865%2C47.514882&extra_info=tollways&optimized=true&options=%7B%22avoid_countries%22%3A+%2211%22%7D&preference=fastest&profile=driving-hgv&api_key=58d904a497c67e00015b45fc2a6b6872037d44119582ef40cdf264c4')
route2_tollhgv = r.json()

toll_values = [(extras['extras']['tollways']['values']) for extras in route2_tollhgv['routes']] # 0 = no tollway, 1 = tollway
route_kombi_hgv = {'toll_values': toll_values, 'route1': route_tollhgv_json} # combining informations in one variable -> coordinates and waypoints

# tollroads
toll_waypoints = [] # array with tollroad waypoints
for value in route_kombi_hgv['toll_values'][0]:
    if 1 in value: # 1 = tollway
        toll_waypoints += [value[0:2]]

toll_coords = []  # waypoints' coordinates
for i, j in toll_waypoints: 
    toll_coords += [(coords['geometry']['coordinates'][i:j]) for coords in route_kombi_hgv['route1']['features']] 

coords = [] # swapping lat and long
for n in toll_coords:
    coords += [[[y,x] for x,y in n]] 

folium.PolyLine(coords, color='#cc0000', popup='Tollroad').add_to(tollhgv_group) # adding to map #red roads
tollhgv_group.add_to(map1)
map1

In [12]:
# requesting data
route_tollcar = directions(client=clnt, dry_run=True, coordinates=(start, destination), profile='driving-car', preference='fastest', extra_info={'tollways'}, options={'avoid_countries':'11'})

url:
https://api.openrouteservice.org/directions?coordinates=11.544056%2C48.151543%7C19.092865%2C47.514882&extra_info=tollways&optimized=true&options=%7B%22avoid_countries%22%3A+%2211%22%7D&preference=fastest&profile=driving-car&api_key=58d904a497c67e00015b45fc2a6b6872037d44119582ef40cdf264c4
Parameters:
{'headers': {'User-Agent': 'ORSClientPython.v0.3', 'Content-type': 'application/json'}, 'timeout': None}


In [17]:
# requesting extra infos for toll waypoints
f = requests.get(url='https://api.openrouteservice.org/directions?coordinates=11.544056%2C48.151543%7C19.092865%2C47.514882&extra_info=tollways&optimized=true&options=%7B%22avoid_countries%22%3A+%2211%22%7D&preference=fastest&profile=driving-car&api_key=58d904a497c67e00015b45fc2a6b6872037d44119582ef40cdf264c4')
route2_tollcar = f.json()

tollcar_values = [(extras['extras']['tollways']['values']) for extras in route2_tollcar['routes']] # 0 = no tollway, 1 = tollway
route_kombi_car = {'toll_values': tollcar_values, 'route1': route_tollcar_json} # combining informations in one variable -> coordinates and waypoints

# tollroads
tollcar_waypoints = [] # array with tollroad waypoints
for value in route_kombi_car['toll_values'][0]:
    if 1 in value: # 1 = tollway
        tollcar_waypoints += [value[0:2]]

tollcar_coords = []  # waypoints' coordinates
for i, j in tollcar_waypoints: 
    tollcar_coords += [(coords['geometry']['coordinates'][i:j]) for coords in route_kombi_car['route1']['features']] 

coords_car = [] # swapping lat and long
for n in tollcar_coords:
    coords_car += [[[y,x] for x,y in n]] 

folium.PolyLine(coords_car, color='#cc0000', popup='Tollroad').add_to(tollcar_group) # adding to map #red roads
tollcar_group.add_to(map1)
map1

In [19]:
map1.add_child(folium.map.LayerControl()) # create Layer Control to switch on and off each location